In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.optimize import curve_fit
from matplotlib.cm import get_cmap

# Alltoall 

In [ ]:
df_multinode = pd.read_csv("../data/data-multi-defand100cflag.csv",delimiter = ",")
df_multinode['benchmark_type'].unique()
df_gather = df_multinode[df_multinode["benchmark_type"]=="Bcast"][df_multinode['msg_size_bytes']>1024][df_multinode['off_cache_flag']==-1]
df_gather.columns.tolist()

: 

In [ ]:
def model(proc_num, alpha, beta, msg_size):
    return (alpha * msg_size * (proc_num - 72) * 72) / (12.5 * 1e3) + 1e6*beta

results = []
msg_sizes = sorted(df_gather['msg_size_bytes'].unique())
n_rows = int(np.ceil(len(msg_sizes) / 3))
n_cols = min(len(msg_sizes), 3)
fig, axes = plt.subplots(n_rows, n_cols, figsize=(5*n_cols, 4*n_rows), squeeze=False)
cmap = get_cmap('tab10')

for idx, (msg_size, group) in enumerate(df_gather.groupby('msg_size_bytes')):
    x = group['proc_num'].values.copy()
    y = group['t_avg_usec'].values.copy()
    sorted_indices = np.argsort(x)
    x = x[sorted_indices]
    y = y[sorted_indices]
    fit_func = lambda proc_num, alpha, beta: model(proc_num, alpha, beta, msg_size)
    popt, _ = curve_fit(fit_func, x, y, bounds=([1, 0], [np.inf, np.inf]))
    alpha, beta = popt
    results.append({'msg_size_bytes': msg_size, 'alpha': alpha, 'beta': beta})

    x_fit = np.linspace(min(x), max(x), 100)
    y_fit = fit_func(x_fit, alpha, beta)
    y_speed = model(x_fit,1,0,msg_size)
    row, col = divmod(idx, n_cols)
    ax = axes[row][col]

    color = cmap(idx % 10)
    # ax.scatter(x, y/1e6, label='Data', color=color)
    ax.plot(x, y/1e6, label='Data', color=color)
    # ax.plot(x_fit, y_fit/1e6, linestyle='--', color=color, alpha=0.5, label='Fit')
    # ax.plot(x_fit, y_speed/1e6, linestyle='--', color='red', alpha=0.1, label='Fit')
    ax.set_title(f'msg_size: {msg_size} bytes')
    ax.set_xlabel('num. proc.')
    ax.set_ylabel('Average Time [s]')
    ax.set_xticks(x)
    ax.grid(True)
    max_data =(x[-1]-72)*72*msg_size
    min_data =(x[0]-72)*72*msg_size

    textstr = ""
    # if(max_data > 1e9):
    #     textstr+=f"max data = {max_data/1e9:0.2f}GB\n" 
    # else:
    #     textstr+=f"max data = {max_data/1e6:0.2f}MB\n" 

    # if(min_data > 1e9):
    #     textstr+=f"min data = {min_data/1e9:0.2f}GB\n" 
    # else:
    #     textstr+=f"min data = {min_data/1e6:0.2f}MB\n" 
    # textstr += r"$\alpha$" +f"= {alpha:.3e}\n"+r"$b_{eff}=$"+f"{12.5/alpha:0.3f}Gbps\n"+\
    #            r"$\beta$"+f"= {beta:.3e} s"
    # ax.text(0.95, 0.05, textstr, transform=ax.transAxes,
    #         fontsize=10, verticalalignment='bottom',
    #         horizontalalignment='right',
    #         bbox=dict(boxstyle='round', facecolor='white', alpha=0.8))

fig.suptitle('Alltoall Time Fit per Message Size\nDots = Data Points | Dashed Lines = Fits\n off_mem=-1', fontsize=14)
fig.tight_layout(rect=[0, 0.03, 1, 0.95])
# plt.savefig("plots/alltoall_analysis.png",dpi=300)
plt.show()

fit_results = pd.DataFrame(results)
fit_results['inv_alpha'] = 1 / fit_results['alpha']
print(fit_results)


: 

In [ ]:
df_gather[df_gather['msg_size_bytes']==1048576]

: 